## System Description
1. We have a set of COFs from a database. Each COF is characterized by a feature vector $$x_{COF} \in X \subset R^d$$ were d=14.


2. We have **two different types** of simulations to calculate **the same material property $S_{Xe/Kr}$**. Therefore, we have a Single-Task/Objective 
$$argmax_{x_{COF} \in X}[S_{Xe/Kr}(x_{COF})]$$

3. Multi-Fidelity problem. 
    1. low-fidelity  => Henry coefficient calculation - MC integration: $S_{Xe/Kr} = \frac{H_{Xe}}{H_{Kr}}$
    2. high-fidelity => GCMC mixture simulation - 80:20 (Kr:Xe) at 298 K and 1.0 bar: $S_{Xe/Kr} = \frac{n_{Xe} / n_{Kr}}{y_{Xe}/y_{Kr}}$


3. We will initialize the system with a few COFs at **both** fidelities in order to initialize the Covariance Matrix.
    1. The fist COF will be the one closest to the center of the normalized feature space
    2. The rest will be chosen to maximize diversity of the training set


4. Each surrogate model will **only train on data acquired at its level of fidelity** (Heterotopic data). $$X_{lf} \neq X_{hf} \subset X$$
    1. We  use the augmented-EI (aEI) acquisition function from [here](https://link.springer.com/content/pdf/10.1007/s00158-005-0587-0.pdf)
    2. Botorch GP surrogate model: [SingleTaskMultiFidelityGP](https://botorch.org/api/models.html#module-botorch.models.gp_regression_fidelity)
    3. Needed to use [this](https://botorch.org/api/optim.html#module-botorch.optim.fit) optimizer to correct matrix jitter
    4. Helpful [tutorial](https://botorch.org/tutorials/discrete_multi_fidelity_bo) for a similar BoTorch Model used

In [1]:
import torch
import gpytorch
from botorch.models import SingleTaskMultiFidelityGP
from botorch.models.transforms.outcome import Standardize
from gpytorch.mlls import ExactMarginalLogLikelihood
from botorch import fit_gpytorch_model
from botorch.optim.fit import fit_gpytorch_torch # fix Cholecky jitter error
from scipy.stats import norm
from sklearn.decomposition import PCA
import math 
import numpy as np
import matplotlib.pyplot as plt
import pickle
import h5py # for .jld2 files
import os
import time

# config plot settings
plt.rcParams["font.size"] = 16

## Load Data

In [2]:
normalization = "min_max_normalization" # "standardization"

In [ ]:
###
#  load data: targets and features
###
if normalization == 'min_max_normalization':
    file = h5py.File("targets_and_normalized_features.jld2", "r")
else:
    file = h5py.File("targets_and_standardized_features.jld2", "r")

# feature matrix
X = torch.from_numpy(np.transpose(file["X"][:]))
# simulation data
y = [torch.from_numpy(np.transpose(file["henry_y"][:])), 
     torch.from_numpy(np.transpose(file["gcmc_y"][:]))]
# associated simulation costs
cost = [np.transpose(file["henry_total_elapsed_time"][:]), 
        np.transpose(file["gcmc_elapsed_time"][:])]

# total number of COFs in data set
nb_COFs = X.shape[0] 

In [2]:
###
#  load data: initializing COFs
###
init_cof_ids_file = pickle.load(open('search_results/{}/initializing_cof_ids.pkl'.format(normalization), 'rb'))
init_cof_ids = init_cof_ids_file['init_cof_ids']

# total number of BO searches to run = number of initializing sets
nb_runs = len(init_cof_ids)

print("raw data - \n\tX:", X.shape)
for f in range(2):
    print("\tfidelity:", f)
    print("\t\ty:", y[f].shape)
    print("\t\tcost: ", cost[f].shape)
    
print("\nEnsure features are normalized - ")
print("max:\n", torch.max(X, 0).values)
print("min:\n", torch.min(X, 0).values)
print("width:\n",torch.max(X, 0).values - torch.min(X, 0).values)

raw data - 
	X: torch.Size([608, 14])
	fidelity: 0
		y: torch.Size([608])
		cost:  (608,)
	fidelity: 1
		y: torch.Size([608])
		cost:  (608,)

Ensure features are normalized - 
max:
 tensor([0.7144, 0.4136, 0.4696, 0.6677, 0.9579, 0.8383, 0.3595, 0.3207, 0.9938,
        0.8242, 0.9692, 0.9869, 0.9868, 0.9762], dtype=torch.float64)
min:
 tensor([-0.2856, -0.5864, -0.5304, -0.3323, -0.0421, -0.1617, -0.6405, -0.6793,
        -0.0062, -0.1758, -0.0308, -0.0131, -0.0132, -0.0238],
       dtype=torch.float64)
width:
 tensor([1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000, 1.0000,
        1.0000, 1.0000, 1.0000, 1.0000, 1.0000], dtype=torch.float64)


In [3]:
print("total high-fidelity cost:", sum(cost[1]).item(), "[min]")
print("total low-fidelity cost: ", sum(cost[0]).item(), "[min]\n")

print("average high-fidelity cost:", np.mean(cost[1]), "[min]")
print("average low-fidelity cost: ", np.mean(cost[0]), "[min]")
print("average cost ratio:\t   ", np.mean(cost[1] / cost[0]))

total high-fidelity cost: 139887.66223703226 [min]
total low-fidelity cost:  10076.305239888028 [min]

average high-fidelity cost: 230.0783918372241 [min]
average low-fidelity cost:  16.57287046034216 [min]
average cost ratio:	    13.444745568580501


## Helper Functions

#### Post-Search Analysis

In [4]:
def calc_fidelity_fraction(acquired_set):
    nb_iters = len(acquired_set)
    fid_frac = np.zeros(nb_iters)
    for i in range(1, nb_iters):
        fid_frac[i] = sum(acquired_set[:, 0][:i+1]) / (i+1)
    return fid_frac

In [5]:
def get_y_maxes_acquired(acquired_set):    
    nb_iters = len(acquired_set)
    y_maxes = np.zeros(nb_iters)
    # we want the maximum y value (only high-fidelity) up to a given iteration
    y_max = 0.0 # update this each iteration.
    for i, (f_id, cof_id) in enumerate(acquired_set):
        y_acq_this_iter = y[f_id][cof_id]
        # i is iteration index
        if f_id == 1 and y_acq_this_iter > y_max:
            y_max = y_acq_this_iter # over-write max
        y_maxes[i] = y_max 
    return y_maxes

In [6]:
def accumulated_cost(cost_acquired):
    nb_iters = len(acquired_set)
    accumulated_cost = np.zeros(nb_iters)
    accumulated_cost[0] = cost_acquired[0]
    for i in range(1, len(cost_acquired)):
        accumulated_cost[i] = accumulated_cost[i-1] + cost_acquired[i]
    return accumulated_cost

#### Construct Initial Inputs

In [7]:
def initialize_acquired_set(X, y, initializing_COFs, discrete_fidelities):
#     cof_ids = diverse_set(X, nb_COFs_initialization) # np.array(ids_train)
    return torch.tensor([[f_id, cof_id] for cof_id in initializing_COFs for f_id in discrete_fidelities])

In [8]:
# construct feature matrix of acquired points
def build_X_train(acquired_set):
    cof_ids = [a[1] for a in acquired_set]
    f_ids = torch.tensor([a[0] for a in acquired_set])
    return torch.cat((X[cof_ids, :], f_ids.unsqueeze(dim=-1)), dim=1)

# construct output vector for acquired points
def build_y_train(acquired_set):
    return torch.tensor([y[f_id][cof_id] for f_id, cof_id in acquired_set]).unsqueeze(-1)

# construct vector to track accumulated cost of acquired points
def build_cost(acquired_set):
    return torch.tensor([cost[f_id][cof_id] for f_id, cof_id in acquired_set]).unsqueeze(-1)

# construct vector to track accumulated cost of acquired points
def build_cost_fidelity(acquired_set, fidelity):
    return torch.tensor([cost[f_id][cof_id] for f_id, cof_id in acquired_set if f_id == fidelity]).unsqueeze(-1)

#### test

In [9]:
def test_initializing_functions(X, y):
    ###
    #  construct training sets
    ###
    # list of (cof_id, fid_id)'s
    acquired_set = [[1, 10], [0, 3], [0, 4]]
    
    # Training Sets
    X_train = build_X_train(acquired_set)
    y_train = build_y_train(acquired_set)
    
    ###
    #  test that the constructor functions are working properly
    ###
    assert np.allclose(X[10, :], X_train[0, :14])
    assert X_train[0, 14] == 1
    assert X_train[1, 14] == 0
    assert y_train[0] == y[1][10] # y[fid_id][cof_id]
    assert y_train[2] == y[0][4]
    return

test_initializing_functions(X, y)

### Surrogate Model

In [10]:
def train_surrogate_model(X_train, y_train):
    model = SingleTaskMultiFidelityGP(
        X_train, 
        y_train, 
        outcome_transform=Standardize(m=1), # m is the output dimension
        data_fidelity=X_train.shape[1] - 1
    )   
    mll = ExactMarginalLogLikelihood(model.likelihood, model)
    fit_gpytorch_model(mll, optimizer=fit_gpytorch_torch)
    return model

### Acquisition Function

In [11]:
# calculate posterior mean and variance for a given fidelity
def mu_sigma(model, X, fidelity):
    f = torch.tensor((), dtype=torch.float64).new_ones((nb_COFs, 1)) * fidelity
    X_f = torch.cat((X, f), dim=1) # last col is associated fidelity
    f_posterior = model.posterior(X_f)
    return f_posterior.mean.squeeze().detach().numpy(), np.sqrt(f_posterior.variance.squeeze().detach().numpy())

# get the current best y-value of desired_fidelity in the acquired set
def get_y_max(acquired_set, desired_fidelity):
    return np.max([y[f_id][cof_id] for f_id, cof_id in acquired_set if f_id == desired_fidelity])

In [12]:
###
#  efficient multi-fidelity correlation function
#  corr(y at given fidelity, y at high-fidelity)
#  (see notes)
###
def mfbo_correlation_function(model, X, fidelity):
    # given fidelity
    f   = torch.tensor((), dtype=torch.float64).new_ones((nb_COFs, 1)) * fidelity
    X_f = torch.cat((X, f), dim=1) # last col is associated fidelity
    
    #  high-fidelity
    hf   = torch.tensor((), dtype=torch.float64).new_ones((nb_COFs, 1)) 
    X_hf = torch.cat((X, hf), dim=1) # last col is associated fidelity

    # combine into a single tensor
    X_all_fid = torch.cat((X_f, X_hf), dim=0)
    
    # get variance for each fidelity
    var_f = torch.flatten(model.posterior(X_f).variance)
    var_hf = torch.flatten(model.posterior(X_hf).variance) # variance
    
    # posterior covariance 
    cov = torch.diag(model(X_all_fid).covariance_matrix[:X_f.size()[0], X_f.size()[0]:])
    
    corr = cov / (torch.sqrt(var_f) * torch.sqrt(var_hf))
    return corr

In [13]:
###
#  cost ratio
###
def estimate_cost_ratio(fidelity, acquired_set):
    avg_cost_f  = torch.mean(build_cost_fidelity(acquired_set, fidelity))
    avg_cost_hf = torch.mean(build_cost_fidelity(acquired_set, 1))
    cr = avg_cost_hf / avg_cost_f
    return cr.item()

###
#  expected imrovement function, only uses hf
###
def EI_hf(model, X, acquired_set):
    hf_mu, hf_sigma = mu_sigma(model, X, 1)
    y_max = get_y_max(acquired_set, 1)
    
    z = (hf_mu - y_max) / hf_sigma
    explore_term = hf_sigma * norm.pdf(z) 
    exploit_term = (hf_mu - y_max) * norm.cdf(z) 
    ei = explore_term + exploit_term
    return np.maximum(ei, np.zeros(nb_COFs))

###
#  acquisition function
###
def acquisition_scores(model, X, fidelity, acquired_set):
    # expected improvement for high-fidelity
    ei = EI_hf(model, X, acquired_set) 
    
    # augmenting functions
    corr_f1_f0 = mfbo_correlation_function(model, X, fidelity)
    
    cr = estimate_cost_ratio(fidelity, acquired_set)

    scores = torch.from_numpy(ei) * corr_f1_f0 * cr
    return scores.detach().numpy()

def in_acquired_set(f_id, cof_id, acquired_set):
    for this_f_id, this_cof_id in acquired_set:
        if this_cof_id == cof_id and this_f_id == f_id:
            return True
    return False

### Bayesian Algorithm

In [14]:
def run_Bayesian_optimization(nb_iterations, initializing_COFs, verbose=False):
    assert nb_iterations > len(initializing_COFs)
    ###
    #  initialize system
    ###
    acquired_set = initialize_acquired_set(X, y, initializing_COFs, discrete_fidelities)
    
    ###
    #  itterate through remaining budget using BO
    ###
    for i in range(nb_COFs_initialization * len(discrete_fidelities), nb_iterations): 
        print("BO iteration: ", i)
        ###
        #  construct training data (perform experiments)
        ###
        X_train = build_X_train(acquired_set)
        y_train = build_y_train(acquired_set)

        if verbose:
            print("Initialization - \n")
            print("\tid acquired = ", [acq_[0].item() for acq_ in acquired_set])
            print("\tfidelity acquired = ", [acq_[1].item() for acq_ in acquired_set])
            print("\tcosts acquired = ", build_cost(acquired_set), " [min]")

            print("\n\tTraining data:\n")
            print("\t\t X train shape = ", X_train.shape)
            print("\t\t y train shape = ", y_train.shape)
            print("\t\t training feature vector = \n", X_train)
        
        ###
        #  train Model
        ###
        model = train_surrogate_model(X_train, y_train)

        ###
        #  acquire new (COF, fidelity) not yet acquired.
        ###
        # entry (fid_id, cof_id) is the acquisition value for fidelity f_id and cof cof_id
        the_acquisition_scores = np.array([acquisition_scores(model, X, f_id, acquired_set) for f_id in discrete_fidelities])
        # overwrite acquired COFs/fidelities with negative infinity to not choose these.
        for f_id, cof_id in acquired_set:
            the_acquisition_scores[f_id, cof_id] = - np.inf
        # select COF/fidelity with highest aquisition score.
        f_id, cof_id = np.unravel_index(np.argmax(the_acquisition_scores), np.shape(the_acquisition_scores))
        assert not in_acquired_set(f_id, cof_id, acquired_set)
        # update acquired_set
        acq = torch.tensor([[f_id, cof_id]], dtype=int)
        acquired_set = torch.cat((acquired_set, acq))

        ###
        #  print useful info
        ###
        if verbose:
            print("\tacquired COF ", cof_id, " at fidelity, ", f_id)
            print("\t\ty = ", y[f_id][cof_id].item())
            print("\t\tcost = ", cost[f_id][cof_id])
        
    return acquired_set

# Run MFBO

In [15]:
###
#  construct initial inputs
###
discrete_fidelities = [0, 1] # set of discrete fidelities to select from
nb_COFs_initialization = 3   # at each fidelity, number of COFs to initialize with
nb_iterations = 150          # BO budget, includes initializing COFs


for j, initializing_COFs in enumerate(init_cof_ids): 
    # check the length of each initializing set
    assert len(initializing_COFs) == nb_COFs_initialization
    print("run #: {}".format(j))
    
    # start timer for BO run
    start_time = time.time()
    ###
    #  run BO search
    ###
    acquired_set = run_Bayesian_optimization(nb_iterations, initializing_COFs)
    
    ###
    #  post-run analysis
    ###
    elapsed_time  = time.time() - start_time
    print("elapsed_time:\t", elapsed_time / 60, " min.")
    y_acquired    = build_y_train(acquired_set)
    y_maxes_acq   = get_y_maxes_acquired(acquired_set.detach().numpy())
    fid_fraction  = calc_fidelity_fraction(acquired_set.detach().numpy())
    cost_acquired = build_cost(acquired_set)
    acc_cost      = accumulated_cost(cost_acquired.flatten().detach().numpy())
    
    ###
    # look at unique COFs acquired
    ###
    # cof_ids_acquired = torch.tensor([acq[1] for acq in acquired_set])
    n_unique_cofs_acquired = len(np.unique([acq[1] for acq in acquired_set]))
    print("total number of unique COFs acquired", n_unique_cofs_acquired)

    ###
    #  Iterations until top COF and accumulated 
    ###
    cof_id_with_max_selectivity = np.argmax(y[1])
    BO_iter_top_cof_acquired = float("inf") # dummy 
    for i, (f_id, cof_id) in enumerate(acquired_set):
        if cof_id == cof_id_with_max_selectivity and f_id == 1:
            BO_iter_top_cof_acquired = i
            print("woo, top COF acquired!")
            print("iteration we acquire top COF = ", BO_iter_top_cof_acquired) 
            break
        elif i == len(acquired_set)-1:
            print("oh no, top COF not acquired!")


    top_cof_acc_cost = sum(build_cost(acquired_set)[:BO_iter_top_cof_acquired])
    print("accumulated cost up to observation of top COF = ", top_cof_acc_cost.item(), " [min]")
    
    ###
    #  store results
    ###
    mfbo_res = dict({'acquired_set': acquired_set.detach().numpy(),
                     'y_acquired': y_acquired.detach().numpy(),
                     'y_max_acquired': y_maxes_acq,
                     'fidelity_fraction': fid_fraction,
                     'cost_acquired': cost_acquired.flatten().detach().numpy(),
                     'accumulated_cost': acc_cost / 60,
                     'nb_COFs_initialization': nb_COFs_initialization,
                     'BO_iter_top_cof_acquired': BO_iter_top_cof_acquired,
                     'elapsed_time (min)':  elapsed_time / 60
                    })

    with open('search_results/{}/mfbo_results/mfbo_results_run_{}.pkl'.format(normalization, j), 'wb') as file:
        pickle.dump(mfbo_res, file)

run #: 0
BO iteration:  6
Iter 10/100: 8.649966451577285
Iter 20/100: 6.26206755970746
Iter 30/100: 4.9909465606677434
Iter 40/100: 4.18377881356157
Iter 50/100: 3.969026411594752
Iter 60/100: 3.8593285725557678
Iter 70/100: 3.814466705392395
Iter 80/100: 3.7929741679094255
Iter 90/100: 3.7831518794269083
Iter 100/100: 3.7761276175238065
BO iteration:  7
Iter 10/100: 7.632250650920198
Iter 20/100: 5.572069981168265
Iter 30/100: 4.456094986634148
Iter 40/100: 3.7145561522884245
Iter 50/100: 3.5556454359205065
Iter 60/100: 3.470555955829871
Iter 70/100: 3.4310039381264614
Iter 80/100: 3.411292441021827
Iter 90/100: 3.3999351933715007
Iter 100/100: 3.390423229014288
BO iteration:  8
Iter 10/100: 6.865587544981905
Iter 20/100: 5.048079508976835
Iter 30/100: 4.053556062111394
Iter 40/100: 3.394821216999607
Iter 50/100: 3.256478428924538
Iter 60/100: 3.1839070521364006
Iter 70/100: 3.149884353225813
Iter 80/100: 3.1318081591753666
Iter 90/100: 3.12087039121823
Iter 100/100: 3.111227455059997

Iter 50/100: 1.659664898167215
Iter 60/100: 1.6350261981592396
Iter 70/100: 1.6166373904455664
Iter 80/100: 1.611023423180747
Iter 90/100: 1.609289650390877
Iter 100/100: 1.6085835206074548
BO iteration:  35
Iter 10/100: 2.7459120552871163
Iter 20/100: 2.2495388398159792
Iter 30/100: 1.9553973665286635
Iter 40/100: 1.7581737779911357
Iter 50/100: 1.6414194137665477
Iter 60/100: 1.6183027825922542
Iter 70/100: 1.600171208781731
Iter 80/100: 1.5947553044041565
Iter 90/100: 1.5929448161186495
Iter 100/100: 1.5922733620158562
BO iteration:  36
Iter 10/100: 2.7090660862032254
Iter 20/100: 2.2225159593540287
Iter 30/100: 1.9307742176682494
Iter 40/100: 1.7374937262417909
Iter 50/100: 1.622223799095158
Iter 60/100: 1.5993937258521982
Iter 70/100: 1.581449057652562
Iter 80/100: 1.576040954512128
Iter 90/100: 1.5741822884167822
Iter 100/100: 1.5734333434062773
BO iteration:  37
Iter 10/100: 2.6739500286360807
Iter 20/100: 2.196673869536121
Iter 30/100: 1.9073206031181897
Iter 40/100: 1.71743680

BO iteration:  59
Iter 10/100: 2.210861544735932
Iter 20/100: 1.8618528336556694
Iter 30/100: 1.610756890360693
Iter 40/100: 1.4168018793429
Iter 50/100: 1.3598484171185563
Iter 60/100: 1.3182723325167054
Iter 70/100: 1.3093209139248407
Iter 80/100: 1.3044754381631831
Iter 90/100: 1.3023353706734293
Iter 100/100: 1.3017985033968587
BO iteration:  60
Iter 10/100: 2.1978385699771694
Iter 20/100: 1.8524026000892548
Iter 30/100: 1.6022907325675828
Iter 40/100: 1.4078147609757934
Iter 50/100: 1.3522176885954797
Iter 60/100: 1.3104084439312993
Iter 70/100: 1.301435025557695
Iter 80/100: 1.2965797779972292
Iter 90/100: 1.2944411629859123
Iter 100/100: 1.2938662386675825
BO iteration:  61
Iter 10/100: 2.1841134031481135
Iter 20/100: 1.8418612069147822
Iter 30/100: 1.591817242472893
Iter 40/100: 1.3959557183060662
Iter 50/100: 1.3424259420385893
Iter 60/100: 1.3005207212916303
Iter 70/100: 1.2915505491998611
Iter 80/100: 1.2863061250739085
Iter 90/100: 1.2840054004563144
Iter 100/100: 1.2832938

Iter 40/100: 1.2057842856865173
Iter 50/100: 1.1057512552898008
Iter 60/100: 1.0911174986211993
Iter 70/100: 1.0849659315147258
Iter 80/100: 1.080961214695197
Iter 90/100: 1.0801219654994603
Iter 100/100: 1.079813755592927
BO iteration:  85
Iter 10/100: 1.9619168817092276
Iter 20/100: 1.6751500826170274
Iter 30/100: 1.4347982551471914
Iter 40/100: 1.202430318606968
Iter 50/100: 1.103370772594489
Iter 60/100: 1.0882062070480767
Iter 70/100: 1.0821578912166894
Iter 80/100: 1.0779312460976962
Iter 90/100: 1.0772145911647413
Iter 100/100: 1.076835359370803
BO iteration:  86
Iter 10/100: 1.9555442568031807
Iter 20/100: 1.6707055025359958
Iter 30/100: 1.4311638093645016
Iter 40/100: 1.1983766174377388
Iter 50/100: 1.1001088352393218
Iter 60/100: 1.0854043527594006
Iter 70/100: 1.0791040923653625
Iter 80/100: 1.0751308142354503
Iter 90/100: 1.0739639143631907
Iter 100/100: 1.0735155616610685
BO iteration:  87
Iter 10/100: 1.949551931884982
Iter 20/100: 1.6665466936176736
Iter 30/100: 1.427779

Iter 40/100: 1.1822018571108788
Iter 50/100: 1.1152222108118086
Iter 60/100: 1.1006039248982975
Iter 70/100: 1.0946607001615465
Iter 80/100: 1.0912125113186535
Iter 90/100: 1.0905800113301742
Iter 100/100: 1.0901994507420967
BO iteration:  116
Iter 10/100: 1.803362419391325
Iter 20/100: 1.5579283461279687
Iter 30/100: 1.3304218700012627
Iter 40/100: 1.1672352491804037
Iter 50/100: 1.1086864686176205
Iter 60/100: 1.092069148465802
Iter 70/100: 1.08404481296926
Iter 80/100: 1.080662164697901
Iter 90/100: 1.0799455236958642
Iter 100/100: 1.0796053141093866
BO iteration:  117
Iter 10/100: 1.796955431819004
Iter 20/100: 1.5506460945295302
Iter 30/100: 1.3190765764771544
Iter 40/100: 1.150313304995128
Iter 50/100: 1.0953402027362114
Iter 60/100: 1.0749266851607053
Iter 70/100: 1.0649491029407316
Iter 80/100: 1.0609296377614836
Iter 90/100: 1.0599435221768598
Iter 100/100: 1.0594439265737192
BO iteration:  118
Iter 10/100: 1.7927826103005504
Iter 20/100: 1.547114698497616
Iter 30/100: 1.31442

...

Iter 50/100: 1.422128590378954
Iter 60/100: 1.292583080732486
Iter 70/100: 1.2547557661467486
Iter 80/100: 1.2431846187413622
Iter 90/100: 1.2375269385940482
Iter 100/100: 1.2364973531786592
BO iteration:  43
Iter 10/100: 2.4742791788190184
Iter 20/100: 2.0484247405335845
Iter 30/100: 1.7660146454026393
Iter 40/100: 1.5841893187526943
Iter 50/100: 1.3951964589230919
Iter 60/100: 1.2837901694266556
Iter 70/100: 1.2448658373601171
Iter 80/100: 1.2368559427093488
Iter 90/100: 1.2314837307415913
Iter 100/100: 1.2303680043931011
BO iteration:  44
Iter 10/100: 2.4523874761888114
Iter 20/100: 2.033028809818104
Iter 30/100: 1.754963262355215
Iter 40/100: 1.5771252526260653
Iter 50/100: 1.3964887482607629
Iter 60/100: 1.2806727259440402
Iter 70/100: 1.2429199606517407
Iter 80/100: 1.2341539607805438
Iter 90/100: 1.2285437495273865
Iter 100/100: 1.2274930205983834
BO iteration:  45
Iter 10/100: 2.4388835401644995
Iter 20/100: 2.0290483817681264
Iter 30/100: 1.7664677940663511
Iter 40/100: 1.6054

Iter 60/100: 1.194812173859457
Iter 70/100: 1.177968085265986
Iter 80/100: 1.1718204427871257
Iter 90/100: 1.169519767591843
Iter 100/100: 1.1688486756559657
BO iteration:  68
Iter 10/100: 2.0943060265884696
Iter 20/100: 1.7764561515218305
Iter 30/100: 1.5402220521942513
Iter 40/100: 1.3975836684301932
Iter 50/100: 1.298940342680775
Iter 60/100: 1.1951580583759698
Iter 70/100: 1.1763317358013963
Iter 80/100: 1.1689157358770506
Iter 90/100: 1.1651982811637753
Iter 100/100: 1.1644478455465301
BO iteration:  69
Iter 10/100: 2.0853631142203928
Iter 20/100: 1.770117177087023
Iter 30/100: 1.5349306240123097
Iter 40/100: 1.3924649367822493
Iter 50/100: 1.2936012015915752
Iter 60/100: 1.1911468302343642
Iter 70/100: 1.1720269217391908
Iter 80/100: 1.164838534817711
Iter 90/100: 1.1612514276229067
Iter 100/100: 1.1604167203733404
BO iteration:  70
Iter 10/100: 2.0742336019943814
Iter 20/100: 1.7609212371385337
Iter 30/100: 1.5249132624777368
Iter 40/100: 1.3827008631280144
Iter 50/100: 1.287660

BO iteration:  92
Iter 10/100: 1.9060151721278105
Iter 20/100: 1.631205579367671
Iter 30/100: 1.389942452546723
Iter 40/100: 1.2122428217139765
Iter 50/100: 1.1356856028631066
Iter 60/100: 1.0708821092610277
Iter 70/100: 1.0646623451409274
Iter 80/100: 1.0609067574563005
Iter 90/100: 1.0593407648134794
Iter 100/100: 1.05871264027878
BO iteration:  93
Iter 10/100: 1.900704782148135
Iter 20/100: 1.6274748174519371
Iter 30/100: 1.386687637446694
Iter 40/100: 1.2087364680328512
Iter 50/100: 1.1325717874346368
Iter 60/100: 1.0687412282573414
Iter 70/100: 1.0626364740635317
Iter 80/100: 1.0590069137364544
Iter 90/100: 1.0574288301490493
Iter 100/100: 1.0568137720500155
BO iteration:  94
Iter 10/100: 1.8950584786090714
Iter 20/100: 1.6234683708545312
Iter 30/100: 1.3832095290015174
Iter 40/100: 1.2073750267871703
Iter 50/100: 1.1308164340554991
Iter 60/100: 1.0680146518236433
Iter 70/100: 1.0613876144269523
Iter 80/100: 1.0577936845870077
Iter 90/100: 1.0563431389165014
Iter 100/100: 1.055761

Iter 80/100: 0.9944261811471659
Iter 90/100: 0.9930270136482708
Iter 100/100: 0.9924018522034588
BO iteration:  117
Iter 10/100: 1.7894996621181884
Iter 20/100: 1.542240658381043
Iter 30/100: 1.3029719016410382
Iter 40/100: 1.1188968918964919
Iter 50/100: 1.0488171753907374
Iter 60/100: 1.0081145921802246
Iter 70/100: 0.9958324586024254
Iter 80/100: 0.9914596624996556
Iter 90/100: 0.9900581684386818
Iter 100/100: 0.9894377005002162
BO iteration:  118
Iter 10/100: 1.7862102924490948
Iter 20/100: 1.5402591078755967
Iter 30/100: 1.3026508212954515
Iter 40/100: 1.126334422303052
Iter 50/100: 1.0576986267671111
Iter 60/100: 1.014322480063103
Iter 70/100: 1.0027946022176568
Iter 80/100: 0.9984998422246287
Iter 90/100: 0.9970420443240255
Iter 100/100: 0.9963742418450857
BO iteration:  119
Iter 10/100: 1.7823275885102192
Iter 20/100: 1.537195692882349
Iter 30/100: 1.299267055640767
Iter 40/100: 1.1211708877221358
Iter 50/100: 1.052287645876435
Iter 60/100: 1.0117712414553772
Iter 70/100: 0.999

BO iteration:  145
Iter 10/100: 1.6970444024107192
Iter 20/100: 1.4656653897342913
Iter 30/100: 1.2175337966462951
Iter 40/100: 1.006502557636545
Iter 50/100: 0.944539807942063
Iter 60/100: 0.9275451606992425
Iter 70/100: 0.922775572069943
Iter 80/100: 0.9200817228373135
Iter 90/100: 0.919222801766367
Iter 100/100: 0.9189561743152405
BO iteration:  146
Iter 10/100: 1.6945051205038109
Iter 20/100: 1.4637001167177026
Iter 30/100: 1.215508434180557
Iter 40/100: 1.0031902227272658
Iter 50/100: 0.9407597955440616
Iter 60/100: 0.9233678591799319
Iter 70/100: 0.9192107167244687
Iter 80/100: 0.9166087871455401
Iter 90/100: 0.9158303683453473
Iter 100/100: 0.915393765757261
BO iteration:  147
Iter 10/100: 1.6921665673529593
Iter 20/100: 1.4619051057256018
Iter 30/100: 1.2137169039975906
Iter 40/100: 1.0014425149218982
Iter 50/100: 0.9387089636971221
Iter 60/100: 0.9216194669994692
Iter 70/100: 0.9174273676815385
Iter 80/100: 0.9148053173737076
Iter 90/100: 0.9140367411721434
Iter 100/100: 0.913